In [34]:
import mysql.connector
import pandas as pd

mydb = mysql.connector.connect(
    host= "localhost",
    user= "root",
    password= "root",
    database= "st"
)
sql_query = "SELECT * FROM coord"

# Execute the SQL query
cursor = mydb.cursor()
cursor.execute(sql_query)

rows = cursor.fetchall()
column_names = [desc[0] for desc in cursor.description]

df = pd.DataFrame(rows, columns=column_names)
cursor.close()
mydb.close()


In [114]:
trip_ids_only_in_df1 = set(trip_ids_only_in_df1)
error_trip_ids_with_quotes = {str(trip_id) for trip_id in trip_ids_only_in_df1}
print("trip_ids_only_in_df1", error_trip_ids_with_quotes )
tierror = set(tierror)

twierror = sorted(error_trip_ids_with_quotes - tierror)
print("with problems", twierror)
print(len(twierror))


trip_ids_only_in_df1 {'2516', '2526', '1724', '2721', '1232', '2817', '2824', '652', '710', '2390', '1581', '2531', '2178', '1887', '1377', '952', '1002', '1477', '2401', '1407', '2144', '1400', '2042', '751', '1476', '1838', '2765', '2515', '396', '298', '1392', '871', '928', '2495', '2814', '2348', '1250', '1375', '2698', '2820', '1499', '2306', '583', '2398', '1609', '1359', '474', '1842', '1192', '402', '1691', '2476', '938', '1546', '787', '2571', '2212', '1627', '451', '2802', '506', '1662', '2359', '2503', '1792', '953', '1672', '2108', '924', '2501', '1442', '932', '927', '2823', '925', '690', '463', '904', '926', '2542', '1634', '1380', '2395', '2322', '2389', '1324', '2399', '1399', '2530', '2753', '1720', '2207', '786', '174', '1393', '2597', '1931', '414', '1728', '1494', '1690', '2292', '1705', '1469', '1666', '2181', '490', '1593', '173', '2065', '750', '249', '711', '2345', '403', '2539', '1383', '1763', '923', '939', '810', '2562', '2546', '1730', '1737', '2750', '616',

In [116]:
print(tierror)

{'1838', '1232', '2108', '2292', '1324', '2765', '2718', '1469', '932', '2212', '1666', '583', '2753', '2181', '1302', '451', '1842', '1192', '402', '1002', '2503', '2144'}


In [117]:
print("with problems", twierror)

with problems ['1113', '1250', '1359', '1375', '1377', '1380', '1383', '1392', '1393', '1399', '1400', '1407', '1442', '1443', '1476', '1477', '1494', '1499', '1546', '1581', '1593', '1609', '1627', '1634', '1662', '1672', '1690', '1691', '1705', '1715', '1720', '1724', '1728', '173', '1730', '1736', '1737', '174', '1763', '1792', '1887', '1931', '1974', '2042', '2065', '2134', '2178', '2207', '2306', '2322', '2345', '2348', '2359', '2389', '2390', '2395', '2398', '2399', '2401', '2433', '2476', '249', '2495', '2498', '2501', '2515', '2516', '2526', '2530', '2531', '2539', '2542', '2546', '2562', '2571', '2585', '2597', '2698', '2721', '2750', '2802', '2814', '2817', '2820', '2823', '2824', '292', '296', '298', '396', '403', '414', '463', '474', '490', '506', '559', '616', '617', '652', '690', '710', '711', '750', '751', '786', '787', '802', '810', '871', '904', '921', '923', '924', '925', '926', '927', '928', '938', '939', '952', '953']


Skipped 200 to 204 Due to some error in 203 please check even 249 since its in another state. Skippped 1002

In [101]:
import requests
import json
import mysql.connector
import numpy as np

def create_pairs(data):
    pairs = []
    first_lat_lng = f"{data.iloc[0]['longitude']},{data.iloc[0]['latitude']}"
    pairs.append(first_lat_lng)
    for i in range(4, len(data), 5):  # Starting from index 9, select every 10th latitude and longitude
        lat_lng = f"{data.iloc[i]['longitude']},{data.iloc[i]['latitude']}"
        pairs.append(lat_lng)
    last_lat_lng = f"{data.iloc[-1]['longitude']},{data.iloc[-1]['latitude']}"
    pairs.append(last_lat_lng)
    return pairs

def cpmini(data):
    pairs = []
    first_lat_lng = f"{data.iloc[0]['longitude']},{data.iloc[0]['latitude']}"
    
    pairs.append(first_lat_lng)
    for i in range(0, len(data)):  # Starting from index 0
        lat_lng = f"{data.iloc[i]['longitude']},{data.iloc[i]['latitude']}"
        pairs.append(lat_lng)
    last_lat_lng = f"{data.iloc[-1]['longitude']},{data.iloc[-1]['latitude']}"
    # if last_lat_lng not in pairs:
    pairs.append(last_lat_lng)
    return pairs

def send_osrm_request(pairs, trip_id, speed, recorded):
    radiuses = ['49'] * len(pairs)
    url = f"http://localhost:5000/match/v1/bicycle/{';'.join(pairs)}?overview=full&radiuses={';'.join(radiuses)}&geometries=geojson&annotations=true"
    response = requests.get(url)
    if response.status_code == 200:
        result = response.json() 
    
        node_id = ""
    
        for match in result['matchings']:
            for leg in match['legs']:
                for n_id in leg['annotation']['nodes']:
                    if node_id:
                        node_id += ","
                    node_id += str(n_id)
            # for point in match['geometry']['coordinates']:
        matched_coordinates.append({'trip_id': trip_id, 'response': result, 'speed': speed, 'recorded': recorded, 'node_id':node_id})
    else:
        print("Error:", response.status_code)
        result = response.json()
        print(result)
        print("Error in Trip_id", trip_id)
        error_trip_ids.append(trip_id)
        print(url)
        print(error_trip_ids)

    return matched_coordinates

matched_coordinates = []
error_trip_ids = []


# batch_data = df[df['trip_id'] == 2]

# pairs = create_pairs(batch_data)
# matched_coordinates_response = send_osrm_request(pairs)

# tid = df['trip_id'].unique()[1002:1003]
tid = tierror 
for i in tid:
    # batch_data = df[df['trip_id'] == i]
    batch_data = df[df['trip_id'] == i]

    if len(batch_data) == 1:

        if len(batch_data) == 1:
            rec = str(batch_data.iloc[0]['recorded'])  # Get the recorded time
            spd = str(batch_data.iloc[0]['speed'])
            node_id = "NA"
            resp = f"{batch_data.iloc[0]['latitude']},{batch_data.iloc[0]['longitude']}"
            matched_coordinates.append({'trip_id': trip_id, 'response': resp, 'speed': spd, 'recorded': rec, 'node_id':node_id})
            print("Response from OSRM API:", matched_coordinates)

    else:

        if len(batch_data) <= 9:
                splitted_dfs = batch_data
                print(f"DataFrames with less than 9 value", splitted_dfs)
                tstmp = ""
                sr = ""
                for k in range(0, len(splitted_dfs)):

                        recorded_time = str(splitted_dfs.iloc[k]['recorded'])  # Get the recorded time
                        if tstmp:  # Check if the string is not empty
                            tstmp += ","  # Add comma separator if needed
                        tstmp += recorded_time

                        speedrng = str(splitted_dfs.iloc[k]['speed'])  # Get the recorded time
                        if sr:  # Check if the string is not empty
                            sr += ","  # Add comma separator if needed
                        sr += speedrng
                
                trip_id = f"{splitted_dfs.iloc[0]['trip_id']}"
                pairs = cpmini(splitted_dfs)
                matched_coordinates = send_osrm_request(pairs, trip_id=trip_id, speed=sr, recorded=tstmp)
        else:

            if 100 >= len(batch_data) > 9:
                sdfs = np.array_split(batch_data, 1)

            elif 500 >= len(batch_data) > 100:
                sdfs = np.array_split(batch_data, 2)

            elif 1000 >= len(batch_data) > 500:
                sdfs = np.array_split(batch_data, 3)

            elif 5000 >= len(batch_data) > 1000:
                sdfs = np.array_split(batch_data, 15)

            elif 10000 >= len(batch_data) > 5000:
                sdfs = np.array_split(batch_data, 30)

            elif 15000 >= len(batch_data) > 10000:
                sdfs = np.array_split(batch_data, 40)

            else:
                sdfs = np.array_split(batch_data, 70)

            for j, df_part in enumerate(sdfs):
                
                print(f"DataFrame {j+1}:\n{df_part}\n")
                timestmp = ""
                speedrange = ""
                for k in range(0, len(df_part), 5):

                        recorded_time = str(df_part.iloc[k]['recorded'])  # Get the recorded time
                        if timestmp:  # Check if the string is not empty
                            timestmp += ","  # Add comma separator if needed
                        timestmp += recorded_time

                        speedrng = str(df_part.iloc[k]['speed'])  # Get the recorded time
                        if speedrange:  # Check if the string is not empty
                            speedrange += ","  # Add comma separator if needed
                        speedrange += speedrng
                
                trip_id = f"{df_part.iloc[0]['trip_id']}"
                # pairs = cp(df_part)
                # matched_coordinates = sor(pairs, trip_id=trip_id, speed=speedrange, recorded=timestmp)
                pairs = create_pairs(df_part)
                matched_coordinates = send_osrm_request(pairs, trip_id=trip_id, speed=speedrange, recorded=timestmp)
                # print("Response from OSRM API:", matched_coordinates_response)
                # print("Response from OSRM API:", matched_coordinates)

print("Response from OSRM API:", matched_coordinates)


DataFrame 1:
        trip_id            recorded   latitude  longitude  altitude  speed  \
715765     1002 2017-10-02 09:04:40  33.764640 -84.306515     286.0   0.00   
715766     1002 2017-10-02 09:04:43  33.764674 -84.306565     286.0   0.00   
715767     1002 2017-10-02 09:04:44  33.764678 -84.306601     276.0   0.00   
715768     1002 2017-10-02 09:04:45  33.764674 -84.306634     278.0   0.00   
715769     1002 2017-10-02 09:04:46  33.764699 -84.306614     274.0   0.00   
...         ...                 ...        ...        ...       ...    ...   
716018     1002 2017-10-02 09:11:00  33.764817 -84.331660     289.0   9.00   
716019     1002 2017-10-02 09:11:01  33.764828 -84.331764     290.0   9.00   
716020     1002 2017-10-02 09:11:02  33.764826 -84.331862     289.0   9.00   
716021     1002 2017-10-02 09:11:03  33.764819 -84.331954     288.0   9.00   
716022     1002 2017-10-02 09:11:04  33.764812 -84.332051     289.0   8.75   

        hAccuracy  vAccuracy  
715765       22.0  

In [106]:
print(matched_coordinates)
unique_list = list(dict.fromkeys(error_trip_ids))

print(unique_list)
print(len(matched_coordinates))

[{'trip_id': '1002', 'response': {'code': 'Ok', 'matchings': [{'confidence': 0.979816, 'geometry': {'coordinates': [[-84.305946, 33.764837], [-84.305986, 33.764917], [-84.305986, 33.764918], [-84.305989, 33.764923], [-84.306117, 33.765179], [-84.306331, 33.765604], [-84.306511, 33.765963], [-84.306587, 33.766115], [-84.306623, 33.766187], [-84.306982, 33.766063], [-84.307312, 33.765948], [-84.307376, 33.765926], [-84.307743, 33.765798], [-84.308018, 33.765702], [-84.308367, 33.765589], [-84.308968, 33.765393], [-84.309066, 33.765369], [-84.309539, 33.765253], [-84.309583, 33.765245], [-84.309833, 33.765202], [-84.310364, 33.765112], [-84.310495, 33.765093], [-84.310602, 33.765076], [-84.310909, 33.765026], [-84.311082, 33.765009], [-84.31115, 33.765003], [-84.311267, 33.764992], [-84.311545, 33.764966], [-84.311571, 33.764964], [-84.311977, 33.764929], [-84.312099, 33.764919], [-84.312446, 33.764891], [-84.312809, 33.76487], [-84.313333, 33.76484], [-84.313503, 33.764827], [-84.313849,

In [107]:
# sql_query = "SELECT * FROM osr WHERE trip_id BETWEEN 1299 AND 1302"

# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # Viewing Table # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 

import mysql.connector
import pandas as pd

mydb = mysql.connector.connect(
    host= "localhost",
    user= "root",
    password= "root",
    database= "st"
)
sql_query = "SELECT * FROM osr"

# Execute the SQL query
cursor = mydb.cursor()
cursor.execute(sql_query)

rows = cursor.fetchall()
column_names = [desc[0] for desc in cursor.description]

df_osr_small = pd.DataFrame(rows, columns=column_names)

# batch_data = df[df['trip_id'] == 1]
# print(len(batch_data['latitude']))

print(df_osr_small)
cursor.close()
mydb.close()

       trip_id                                           response  \
0            1  {"code": "Ok", "matchings": [{"confidence": 0....   
1            1  {"code": "Ok", "matchings": [{"confidence": 0....   
2            1  {"code": "Ok", "matchings": [{"confidence": 0....   
3            2  {"code": "Ok", "matchings": [{"confidence": 0....   
4            2  {"code": "Ok", "matchings": [{"confidence": 0....   
...        ...                                                ...   
17334     1302                 "33.814787920596,-84.332197560076"   
17335     1302                             "33.776246,-84.360049"   
17336     1302                 "33.763074712547,-84.313245719267"   
17337     1302                 "33.769790926983,-84.390549251579"   
17338     1302                 "33.777015900888,-84.294732359163"   

                                                   speed  \
0      1.3200000524521,2.2999999523163,3.319999933242...   
1      4.1199998855591,3.8599998950958,4.25,3.17000

In [ ]:
unique_count = df['trip_id'].nunique()
print("Number of unique values:", unique_count)
batch_data = df[df['trip_id'] == 203]

print(batch_data)

In [ ]:
for record in matched_coordinates:
    trip_id = record['trip_id']
    response = json.dumps(record['response'])  # Convert response to JSON string
    speed = record['speed']
    recorded = record['recorded']
    node_id = record['node_id']
    print(trip_id, response, speed, recorded, node_id)

In [5]:

import mysql.connector

mydb = mysql.connector.connect(
    host= "localhost",
    user= "root",
    password= "root",
    database= "st"
)

create_table_query = """
CREATE TABLE IF NOT EXISTS osr (
    trip_id INT,
    response LONGTEXT,
    speed TEXT,
    recorded TEXT,
    node_id TEXT
)
"""

# Execute the table creation query
cursor = mydb.cursor()
cursor.execute(create_table_query)

insert_query = "INSERT INTO osr (trip_id, response, speed, recorded, node_id) VALUES (%s, %s, %s, %s, %s)"

# Iterate over matched_coordinates and insert each record into the table
for record in matched_coordinates:
    response = json.dumps(record['response'])  # Convert response to JSON string
    cursor.execute(insert_query, (record['trip_id'], response, record['speed'], record['recorded'], record['node_id']))

# Commit changes and close the cursor and MySQL connection
mydb.commit()
cursor.close()
mydb.close()


In [105]:
# -----------------------------updating table--------------------------------


import mysql.connector

mydb = mysql.connector.connect(
    host= "localhost",
    user= "root",
    password= "root",
    database= "st"
)

# Execute the table creation query
cursor = mydb.cursor()


insert_query = "INSERT INTO osr (trip_id, response, speed, recorded, node_id) VALUES (%s, %s, %s, %s, %s)"

# Iterate over matched_coordinates and insert each record into the table
for record in matched_coordinates:
    response = json.dumps(record['response'])  # Convert response to JSON string
    cursor.execute(insert_query, (record['trip_id'], response, record['speed'], record['recorded'], record['node_id']))

# Commit changes and close the cursor and MySQL connection
mydb.commit()
cursor.close()
mydb.close()


In [ ]:
# Update Table

import mysql.connector

mydb = mysql.connector.connect(
    host= "localhost",
    user= "root",
    password= "root",
    database= "st"
)

insert_query = """
INSERT INTO osrmresp (response) 
VALUES (%s) 
ON DUPLICATE KEY UPDATE response = VALUES(response)
"""

# Execute the insertion query
cursor = mydb.cursor()
cursor.execute(insert_query, (json_response,))

mydb.commit()
cursor.close()
mydb.close()

In [102]:
import mysql.connector

mydb = mysql.connector.connect(
    host= "localhost",
    user= "root",
    password= "root",
    database= "st"
)


cursor = mydb.cursor()
# Define the DELETE query to delete rows from index 17315 to the last row
for trip_id in trip_ids_only_in_df1:
    # Define the DELETE query to delete rows with the current trip ID
    delete_query = f"""
        DELETE FROM osr
        WHERE trip_id = {trip_id}
    """
    
    cursor.execute(delete_query)


# Commit changes and close the MySQL connection
mydb.commit()
mydb.close()

In [19]:
print("Response from OSRM API:", json_response)

Response from OSRM API: {"code": "Ok", "matchings": [{"confidence": 0.906154, "geometry": {"coordinates": [[-84.364281, 33.77768], [-84.364234, 33.777681], [-84.364234, 33.777609], [-84.364234, 33.777681], [-84.364281, 33.77768], [-84.364281, 33.77768], [-84.364282, 33.777393], [-84.364283, 33.777279], [-84.364283, 33.777279], [-84.364284, 33.777171], [-84.364284, 33.77701], [-84.364285, 33.776874], [-84.364286, 33.776746], [-84.364308, 33.776745], [-84.364464, 33.776744], [-84.364568, 33.776743], [-84.364568, 33.776743], [-84.364574, 33.776689], [-84.364742, 33.776687], [-84.365276, 33.776677], [-84.365289, 33.776677], [-84.365347, 33.776676], [-84.36515, 33.77587], [-84.364954, 33.775072], [-84.364863, 33.7747], [-84.364783, 33.774248], [-84.364696, 33.773752], [-84.364634, 33.773507], [-84.36462, 33.773451], [-84.364561, 33.773218], [-84.364412, 33.772632], [-84.364382, 33.772521], [-84.364281, 33.772143], [-84.364277, 33.772126], [-84.364229, 33.771991], [-84.364113, 33.77173], [-8

In [94]:
print(type(trip_ids_only_in_df1))

<class 'list'>
